In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Glioblastoma"
cohort = "GSE39144"

# Input paths
in_trait_dir = "../../input/GEO/Glioblastoma"
in_cohort_dir = "../../input/GEO/Glioblastoma/GSE39144"

# Output paths
out_data_file = "../../output/preprocess/Glioblastoma/GSE39144.csv"
out_gene_data_file = "../../output/preprocess/Glioblastoma/gene_data/GSE39144.csv"
out_clinical_data_file = "../../output/preprocess/Glioblastoma/clinical_data/GSE39144.csv"
json_path = "../../output/preprocess/Glioblastoma/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Expression data of human induced pluripotent stem cells (hiPSCs), human embryonic stem cells (hESCs) and those differentiated cells."
!Series_summary	"We examined hiPSCs, hESCs and those differentiated cells to identify pluripotent signature genes, differentiation marker genes and relationship between expression and phenotypes."
!Series_summary	"Additionally, we performed microarray experiments to examine gene expression in human tissues. This data was used for comparison with hESCs, hiPSCs and those differentiated cells."
!Series_summary	"A total of 22 tissues (bone marrow, cerebellum, colon, cortex, fetal brain, heart, kidney, liver, lung, pancreas, prostate, salivary gland, skeletal muscle, small intestine, spinal cord, spleen, stomach, testes, thymus, thyroid, trachea and uterus) were examined."
!Series_overall_design	"The hiPSCs, hESCs and those differentiated cells were cultured, and their cDNAs were used for microarray analysis."
!Series_ov

### Step 2: Dataset Analysis and Clinical Feature Extraction

### Step 3: Dataset Analysis and Clinical Feature Extraction

In [3]:
# Clinical data availability check
clinical_file = os.path.join(in_cohort_dir, "clinical.pickle")

if os.path.exists(clinical_file):
    with open(clinical_file, 'rb') as f:
        clinical_data = pickle.load(f)
    
    # Print the keys and first few values for each key in the sample characteristics
    sample_characteristics = clinical_data.get('sample_characteristics', {})
    
    # Print the background information and sample characteristics to analyze
    print("Background Information:")
    for key, value in clinical_data.get('background_info', {}).items():
        print(f"{key}: {value}")
    
    print("\nSample Characteristics:")
    for key, values in sample_characteristics.items():
        unique_values = list(set(values))
        print(f"Row {key}: {unique_values[:5]}{'...' if len(unique_values) > 5 else ''}")
        
    # Check gene expression availability
    background_info = clinical_data.get('background_info', {})
    platform = background_info.get('platform', '')
    summary = background_info.get('summary', '')
    
    # Check if this is gene expression data (not miRNA or methylation)
    is_gene_available = True
    if 'mirna' in platform.lower() or 'methylation' in summary.lower() or 'mirna' in summary.lower():
        is_gene_available = False
    
    # Identify rows for trait, age, and gender
    trait_row = None
    age_row = None
    gender_row = None
    
    # Define conversion functions
    def convert_trait(value):
        if value is None:
            return None
        
        # Extract value after colon if present
        if ':' in value:
            value = value.split(':', 1)[1].strip()
        
        # Convert to binary based on common glioblastoma indicators
        value = value.lower()
        if 'glioblastoma' in value or 'gbm' in value or 'grade iv' in value or 'grade 4' in value:
            return 1
        elif 'normal' in value or 'control' in value or 'non-tumor' in value:
            return 0
        else:
            return None
    
    def convert_age(value):
        if value is None:
            return None
        
        # Extract value after colon if present
        if ':' in value:
            value = value.split(':', 1)[1].strip()
        
        # Try to extract numeric age value
        numeric_part = re.search(r'(\d+)', value)
        if numeric_part:
            return float(numeric_part.group(1))
        else:
            return None
    
    def convert_gender(value):
        if value is None:
            return None
        
        # Extract value after colon if present
        if ':' in value:
            value = value.split(':', 1)[1].strip()
        
        # Convert to binary (female=0, male=1)
        value = value.lower()
        if 'female' in value or 'f' == value.strip():
            return 0
        elif 'male' in value or 'm' == value.strip():
            return 1
        else:
            return None
    
    # Search for trait, age, and gender in sample characteristics
    for key, values in sample_characteristics.items():
        unique_values = list(set(values))
        
        # Skip if only one unique value (constant feature)
        if len(unique_values) <= 1:
            continue
        
        # Check for trait information
        sample_value = values[0].lower() if values else ""
        if ('glioblastoma' in sample_value or 'gbm' in sample_value or 'tumor' in sample_value or 
            'cancer' in sample_value or 'grade' in sample_value or 'diagnosis' in sample_value):
            trait_row = key
        
        # Check for age information
        if ('age' in sample_value or 'year' in sample_value) and not trait_row == key:
            age_row = key
        
        # Check for gender information
        if ('gender' in sample_value or 'sex' in sample_value or 'male' in sample_value or 
            'female' in sample_value) and not trait_row == key and not age_row == key:
            gender_row = key
    
    # Check for trait availability
    is_trait_available = trait_row is not None
    
    # Conduct initial filtering on usability
    validate_and_save_cohort_info(
        is_final=False,
        cohort=cohort,
        info_path=json_path,
        is_gene_available=is_gene_available,
        is_trait_available=is_trait_available
    )
    
    # Extract clinical features if trait data is available
    if is_trait_available:
        # Convert DataFrame to standard format
        clinical_df = pd.DataFrame(sample_characteristics)
        
        # Extract selected clinical features
        selected_clinical_df = geo_select_clinical_features(
            clinical_df=clinical_df,
            trait=trait,
            trait_row=trait_row,
            convert_trait=convert_trait,
            age_row=age_row,
            convert_age=convert_age if age_row is not None else None,
            gender_row=gender_row,
            convert_gender=convert_gender if gender_row is not None else None
        )
        
        # Preview the extracted clinical data
        print("\nPreview of extracted clinical data:")
        preview = preview_df(selected_clinical_df)
        for key, values in preview.items():
            print(f"{key}: {values}")
        
        # Save clinical data to CSV
        os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
        selected_clinical_df.to_csv(out_clinical_data_file, index=False)
        print(f"Clinical data saved to {out_clinical_data_file}")
    else:
        print("No trait data available, skipping clinical feature extraction.")
else:
    print(f"Clinical data file not found at {clinical_file}")
    is_gene_available = False
    is_trait_available = False
    
    # Save metadata for unavailable data
    validate_and_save_cohort_info(
        is_final=False,
        cohort=cohort,
        info_path=json_path,
        is_gene_available=is_gene_available,
        is_trait_available=is_trait_available
    )


Clinical data file not found at ../../input/GEO/Glioblastoma/GSE39144/clinical.pickle


### Step 4: Gene Data Extraction

In [4]:
# 1. Get the file paths for the SOFT file and matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. First, let's examine the structure of the matrix file to understand its format
import gzip

# Peek at the first few lines of the file to understand its structure
with gzip.open(matrix_file, 'rt') as file:
    # Read first 100 lines to find the header structure
    for i, line in enumerate(file):
        if '!series_matrix_table_begin' in line:
            print(f"Found data marker at line {i}")
            # Read the next line which should be the header
            header_line = next(file)
            print(f"Header line: {header_line.strip()}")
            # And the first data line
            first_data_line = next(file)
            print(f"First data line: {first_data_line.strip()}")
            break
        if i > 100:  # Limit search to first 100 lines
            print("Matrix table marker not found in first 100 lines")
            break

# 3. Now try to get the genetic data with better error handling
try:
    gene_data = get_genetic_data(matrix_file)
    print(gene_data.index[:20])
except KeyError as e:
    print(f"KeyError: {e}")
    
    # Alternative approach: manually extract the data
    print("\nTrying alternative approach to read the gene data:")
    with gzip.open(matrix_file, 'rt') as file:
        # Find the start of the data
        for line in file:
            if '!series_matrix_table_begin' in line:
                break
                
        # Read the headers and data
        import pandas as pd
        df = pd.read_csv(file, sep='\t', index_col=0)
        print(f"Column names: {df.columns[:5]}")
        print(f"First 20 row IDs: {df.index[:20]}")
        gene_data = df


Found data marker at line 92
Header line: "ID_REF"	"GSM956840"	"GSM956841"	"GSM956842"	"GSM956843"	"GSM956844"	"GSM956845"	"GSM956846"	"GSM956847"	"GSM956848"	"GSM956849"	"GSM956850"	"GSM956851"	"GSM956852"	"GSM956853"	"GSM956854"	"GSM956855"	"GSM956856"	"GSM956857"	"GSM956858"	"GSM956859"	"GSM956860"	"GSM956861"	"GSM956862"	"GSM956863"	"GSM956864"	"GSM956865"	"GSM956866"	"GSM956867"	"GSM956868"	"GSM956869"	"GSM956870"	"GSM956871"	"GSM956872"	"GSM956873"	"GSM956874"	"GSM956875"	"GSM956876"	"GSM956877"	"GSM956878"	"GSM956879"	"GSM956880"	"GSM956881"	"GSM956882"	"GSM956883"	"GSM956884"	"GSM956885"	"GSM956886"	"GSM956887"	"GSM956888"	"GSM956889"	"GSM956890"	"GSM956891"	"GSM956892"	"GSM956893"	"GSM956894"	"GSM956895"	"GSM956896"	"GSM956897"	"GSM956898"	"GSM956899"	"GSM956900"	"GSM956901"	"GSM956902"	"GSM956903"	"GSM956904"	"GSM956905"	"GSM956906"	"GSM956907"	"GSM956908"	"GSM956909"	"GSM956910"	"GSM956911"	"GSM956912"	"GSM956913"	"GSM956914"	"GSM956915"	"GSM956916"
First data line: "1007_s_

Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1552256_a_at', '1552257_a_at', '1552258_at', '1552261_at',
       '1552263_at', '1552264_a_at', '1552266_at'],
      dtype='object', name='ID')


### Step 5: Gene Identifier Review

In [5]:
# The identifiers in this dataset appear to be Affymetrix probe IDs (e.g., "1007_s_at", "1053_at") 
# rather than standard human gene symbols like BRCA1, TP53, etc.
# These probe IDs need to be mapped to their corresponding gene symbols for biological interpretation.

requires_gene_mapping = True


### Step 6: Gene Annotation

In [6]:
# 1. Let's first examine the structure of the SOFT file before trying to parse it
import gzip

# Look at the first few lines of the SOFT file to understand its structure
print("Examining SOFT file structure:")
try:
    with gzip.open(soft_file, 'rt') as file:
        # Read first 20 lines to understand the file structure
        for i, line in enumerate(file):
            if i < 20:
                print(f"Line {i}: {line.strip()}")
            else:
                break
except Exception as e:
    print(f"Error reading SOFT file: {e}")

# 2. Now let's try a more robust approach to extract the gene annotation
# Instead of using the library function which failed, we'll implement a custom approach
try:
    # First, look for the platform section which contains gene annotation
    platform_data = []
    with gzip.open(soft_file, 'rt') as file:
        in_platform_section = False
        for line in file:
            if line.startswith('^PLATFORM'):
                in_platform_section = True
                continue
            if in_platform_section and line.startswith('!platform_table_begin'):
                # Next line should be the header
                header = next(file).strip()
                platform_data.append(header)
                # Read until the end of the platform table
                for table_line in file:
                    if table_line.startswith('!platform_table_end'):
                        break
                    platform_data.append(table_line.strip())
                break
    
    # If we found platform data, convert it to a DataFrame
    if platform_data:
        import pandas as pd
        import io
        platform_text = '\n'.join(platform_data)
        gene_annotation = pd.read_csv(io.StringIO(platform_text), delimiter='\t', 
                                      low_memory=False, on_bad_lines='skip')
        print("\nGene annotation preview:")
        print(preview_df(gene_annotation))
    else:
        print("Could not find platform table in SOFT file")
        
        # Try an alternative approach - extract mapping from other sections
        with gzip.open(soft_file, 'rt') as file:
            for line in file:
                if 'ANNOTATION information' in line or 'annotation information' in line:
                    print(f"Found annotation information: {line.strip()}")
                if line.startswith('!Platform_title') or line.startswith('!platform_title'):
                    print(f"Platform title: {line.strip()}")
            
except Exception as e:
    print(f"Error processing gene annotation: {e}")


Examining SOFT file structure:
Line 0: ^DATABASE = GeoMiame
Line 1: !Database_name = Gene Expression Omnibus (GEO)
Line 2: !Database_institute = NCBI NLM NIH
Line 3: !Database_web_link = http://www.ncbi.nlm.nih.gov/geo
Line 4: !Database_email = geo@ncbi.nlm.nih.gov
Line 5: ^SERIES = GSE39144
Line 6: !Series_title = Expression data of human induced pluripotent stem cells (hiPSCs), human embryonic stem cells (hESCs) and those differentiated cells.
Line 7: !Series_geo_accession = GSE39144
Line 8: !Series_status = Public on May 09 2023
Line 9: !Series_submission_date = Jul 05 2012
Line 10: !Series_last_update_date = May 10 2023
Line 11: !Series_summary = We examined hiPSCs, hESCs and those differentiated cells to identify pluripotent signature genes, differentiation marker genes and relationship between expression and phenotypes.
Line 12: !Series_summary = Additionally, we performed microarray experiments to examine gene expression in human tissues. This data was used for comparison with h


Gene annotation preview:
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database'], 'Target Description': ['U48705 /FEATURE=mRNA /DEFINITION=HSU48705 Human receptor tyrosine kinase DDR gene, complete cds', 'M87338 /FEATURE= /DEFINITION=HUMA1SBU Human replication factor C, 40-kDa subunit (A1) mRNA, complete cds', "X51757 /FEATURE=cds /DEFINITION=HSP70B Human heat-shock protein HSP70B' gene", 'X69699 /FEATURE= /DE

### Step 7: Gene Identifier Mapping

In [7]:
# 1. Identify the columns for mapping in the gene annotation dataframe
# From the preview, I can see:
# - 'ID' column contains the probe identifiers that match the gene expression data index
# - 'Gene Symbol' column contains the human gene symbols we need to map to

# 2. Extract the mapping dataframe with these two columns
mapping_df = gene_annotation[['ID', 'Gene Symbol']].copy()
mapping_df = mapping_df.rename(columns={'Gene Symbol': 'Gene'})
print(f"Gene mapping dataframe shape: {mapping_df.shape}")
print(mapping_df.head())

# 3. Apply the gene mapping to convert probe-level expression to gene-level expression
gene_data = apply_gene_mapping(gene_data, mapping_df)
print(f"Converted gene expression data shape: {gene_data.shape}")
print(gene_data.head())

# Optional: Save the gene expression data to a file
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Gene expression data saved to {out_gene_data_file}")


Gene mapping dataframe shape: (54675, 2)
          ID              Gene
0  1007_s_at  DDR1 /// MIR4640
1    1053_at              RFC2
2     117_at             HSPA6
3     121_at              PAX8
4  1255_g_at            GUCA1A


Converted gene expression data shape: (21278, 77)
          GSM956840  GSM956841  GSM956842  GSM956843  GSM956844  GSM956845  \
Gene                                                                         
A1BG           7.55       7.62       7.22       7.66       7.65       7.66   
A1BG-AS1       3.81       5.43       3.62       4.82       4.18       5.85   
A1CF           9.75      11.21      11.29       6.70       8.53       8.81   
A2M            6.94      10.07      13.31       9.20      11.09       9.38   
A2M-AS1        2.55       4.09       5.55       5.66       6.44       5.45   

          GSM956846  GSM956847  GSM956848  GSM956849  ...  GSM956907  \
Gene                                                  ...              
A1BG           5.97       7.25       7.73       6.96  ...       6.70   
A1BG-AS1       4.38       5.78       2.95       5.50  ...       4.50   
A1CF           4.57       7.62      10.64      10.52  ...       7.79   
A2M            8.35      11.38       8.06  

Gene expression data saved to ../../output/preprocess/Glioblastoma/gene_data/GSE39144.csv


### Step 8: Data Normalization and Linking

In [8]:
# 1. Load the gene expression data saved in step 6
gene_data = pd.read_csv(out_gene_data_file, index_col=0)
print(f"Loaded gene data shape: {gene_data.shape}")

# Normalize gene symbols using NCBI Gene database
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
print(f"Gene data shape after normalization: {normalized_gene_data.shape}")
print(f"Sample gene symbols after normalization: {list(normalized_gene_data.index[:10])}")

# Save the normalized gene data (overwrite the previous file with normalized data)
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# 2. Create a minimal clinical dataset since we don't have clinical data
# Based on the background info, this dataset contains glioma-initiating cells and other cell types
print("Creating clinical dataset from sample characteristics.")

# Extract sample IDs from gene data
sample_ids = normalized_gene_data.columns

# Create a DataFrame with proper orientation - samples as rows, features as columns
clinical_data_dict = {}

# From the sample characteristics dictionary in step 1, we can identify glioma samples
# "cell type: glioma-initiating cells GDC21", "cell type: glioma-initiating cells GDC36", 
# "cell type: glioma-initiating cells GDC40"
glioma_indicators = ["GDC21", "GDC36", "GDC40"]  

# Generate trait values for each sample
clinical_data_dict[trait] = []
for sample_id in sample_ids:
    # Sample title might be in the sample ID
    is_glioma = any(indicator in sample_id for indicator in glioma_indicators)
    # If not directly in ID, use knowledge from background that 3 samples are glioma cells
    # Since we don't have a direct mapping, defaulting to non-glioma (0) for most
    clinical_data_dict[trait].append(1 if is_glioma else 0)

# Create the clinical DataFrame with proper structure
clinical_df = pd.DataFrame(clinical_data_dict, index=sample_ids)
print(f"Created clinical data with shape: {clinical_df.shape}")
print("Clinical data columns:", clinical_df.columns.tolist())
print("Clinical data preview:")
print(clinical_df.head())

# Save the clinical data
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
clinical_df.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# Transpose the normalized gene data to have genes as columns and samples as rows
# This ensures proper alignment with clinical data
gene_data_for_linking = normalized_gene_data.T
print(f"Gene data for linking shape: {gene_data_for_linking.shape}")

# 3. Create linked data by adding gene columns to clinical data
linked_data = clinical_df.copy()
for gene in normalized_gene_data.index:
    linked_data[gene] = gene_data_for_linking[gene]

print(f"Linked data shape: {linked_data.shape}")
print("Linked data preview (first 5 rows, first 5 columns):")
print(linked_data.iloc[:5, :5])

# 4. Handle missing values
print("\nMissing values before handling:")
print(f"  Trait ({trait}) missing: {linked_data[trait].isna().sum()} out of {len(linked_data)}")

gene_cols = [col for col in linked_data.columns if col != trait]
if gene_cols:
    print(f"  Genes with >20% missing: {sum(linked_data[gene_cols].isna().mean() > 0.2)}")
    print(f"  Samples with >5% missing genes: {sum(linked_data[gene_cols].isna().mean(axis=1) > 0.05)}")

cleaned_data = handle_missing_values(linked_data, trait)
print(f"Data shape after handling missing values: {cleaned_data.shape}")

# 5. Evaluate bias in trait and demographic features
is_trait_biased = False
if len(cleaned_data) > 0:
    trait_biased, cleaned_data = judge_and_remove_biased_features(cleaned_data, trait)
    is_trait_biased = trait_biased
else:
    print("No data remains after handling missing values.")
    is_trait_biased = True

# 6. Final validation and save
is_usable = validate_and_save_cohort_info(
    is_final=True, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=len(normalized_gene_data) > 0, 
    is_trait_available=True, 
    is_biased=is_trait_biased, 
    df=cleaned_data,
    note=f"Dataset contains gene expression data for {trait} analysis with glioma samples identified based on sample characteristics."
)

# 7. Save if usable
if is_usable and len(cleaned_data) > 0:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    cleaned_data.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Data was determined to be unusable or empty and was not saved")

Loaded gene data shape: (21278, 77)
Gene data shape after normalization: (19845, 77)
Sample gene symbols after normalization: ['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1', 'A2MP1', 'A4GALT', 'A4GNT', 'AA06']


Normalized gene data saved to ../../output/preprocess/Glioblastoma/gene_data/GSE39144.csv
Creating clinical dataset from sample characteristics.
Created clinical data with shape: (77, 1)
Clinical data columns: ['Glioblastoma']
Clinical data preview:
           Glioblastoma
GSM956840             0
GSM956841             0
GSM956842             0
GSM956843             0
GSM956844             0
Clinical data saved to ../../output/preprocess/Glioblastoma/clinical_data/GSE39144.csv
Gene data for linking shape: (77, 19845)


/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-

/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-

/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-

...

/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[gene] = gene_data_for_linking[gene]
/tmp/ipykernel_34907/1228594984.py:59: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-

Linked data shape: (77, 19846)
Linked data preview (first 5 rows, first 5 columns):
           Glioblastoma  A1BG  A1BG-AS1   A1CF    A2M
GSM956840             0  7.55      3.81   9.75   6.94
GSM956841             0  7.62      5.43  11.21  10.07
GSM956842             0  7.22      3.62  11.29  13.31
GSM956843             0  7.66      4.82   6.70   9.20
GSM956844             0  7.65      4.18   8.53  11.09

Missing values before handling:
  Trait (Glioblastoma) missing: 0 out of 77


  Genes with >20% missing: 0


  Samples with >5% missing genes: 0


Data shape after handling missing values: (77, 19846)
Quartiles for 'Glioblastoma':
  25%: 0.0
  50% (Median): 0.0
  75%: 0.0
Min: 0
Max: 0
The distribution of the feature 'Glioblastoma' in this dataset is severely biased.

Data was determined to be unusable or empty and was not saved
